# Web Scraping: Selenium

- Bizler internette bir web sitesine bağlanıp belirli alanlara tıklayarak geziniyor, bazı formlar dolduruyor veya butonlara tıklayarak bazı yeni ekranların karşımıza gelmesini bekliyoruz. İşte **Selenium**, bilgisayarımıza yükleyeceğiniz bir driver yardımıyla ekrana bir tarayıcı açarak, gerçek bir insan gibi istediğimiz işlemleri çalıştırmanızı sağlayan bir araçtır. 

## Dokümantasyon

- [Selenium](https://selenium-python.readthedocs.io/)

## Kütüphane Yükleme

```python
- !pip install selenium
```

## WebDriver Yükleme

Selenium kütüphanesini kullabilmek için bilgisayarlarımıza bir webdriver yüklememiz gerekiyor. Eğer imkanımız varsa **ChromeDriver** bizim için en iyi seçenek olacaktır ancak diğer tarayıcıların driverlarını da kullanabiliriz. Yükleme adımları için aşağıdaki yönergeyi takip edebilirsiniz:

1. Kullandığınız tarayıcınızın versiyonunu öğrenin. (Chrome > About Google Chrome)
2. [Linkteki](https://chromedriver.chromium.org/downloads) adrese giderek tarayıcınızın versiyonuyla uyumlu olan ChromeDriver'ı indirin.
3. İşletim sisteminizle uyumlu olan Driverı indirdikten sonra indirdiğiniz **chromedriver.exe** dosyasını Zip'ten çıkarıp uygun gördüğünüz bir dizine kopyalayın.

In [1]:
from bs4 import BeautifulSoup
import requests
import time, os

In [3]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import warnings
warnings.filterwarnings(action='ignore')

# Bilgisayarımızda chromedriver.exe dosyasını kaydettiğimiz dizin
chromedriver = "/Users/ataozarslan/Documents/chromedriver-mac-arm64/chromedriver"
os.environ["webdriver.chrome.driver"] = chromedriver

## Örnek 1 - YouTube

### Dinamik Sayfalar

Bazı sayfalar içeriklerini dinamik olarak sunarlar, bu da tarayıcıya her yüklendiklerinde farklı görünebilecekleri anlamına gelir. Tarayıcılarımızdaki öğeleri inceleyerek gördüğünüz HTML, erişim anında oluşturulduğundan dolayı `Requests` ve `BeautifulSoup` kütüphaneleri istediğimiz sonucu veremeyebilir.

In [4]:
youtube_query = "https://www.youtube.com/results?search_query=how+to+become+a+data+scientist"

In [5]:
page = requests.get(youtube_query).text
soup = BeautifulSoup(page, "html.parser")

In [6]:
soup

<!DOCTYPE html>
<html darker-dark-theme="" darker-dark-theme-deprecate="" lang="tr-TR" style="font-size: 10px;font-family: Roboto, Arial, sans-serif;" system-icons="" typography="" typography-spacing=""><head><script data-id="_gd" nonce="rTkfTmKK8K0dsydOXi7d6g">window.WIZ_global_data = {"MuJWjd":false,"nQyAE":{},"oxN3nb":{"1":false}};</script><meta content="IE=edge" http-equiv="X-UA-Compatible"/><meta content="ApvK67ociHgr2egd6c2ZjrfPuRs8BHcvSggogIOPQNH7GJ3cVlyJ1NOq/COCdj0+zxskqHt9HgLLETc8qqD+vwsAAABteyJvcmlnaW4iOiJodHRwczovL3lvdXR1YmUuY29tOjQ0MyIsImZlYXR1cmUiOiJQcml2YWN5U2FuZGJveEFkc0FQSXMiLCJleHBpcnkiOjE2OTUxNjc5OTksImlzU3ViZG9tYWluIjp0cnVlfQ==" http-equiv="origin-trial"/><script nonce="rTkfTmKK8K0dsydOXi7d6g">var ytcfg={d:function(){return window.yt&&yt.config_||ytcfg.data_||(ytcfg.data_={})},get:function(k,o){return k in ytcfg.d()?ytcfg.d()[k]:o},set:function(){var a=arguments;if(a.length>1)ytcfg.d()[a[0]]=a[1];else{var k;for(k in a[0])ytcfg.d()[k]=a[0][k]}}};
window.ytcfg.set('EME

İlk olarak video başlıklarına ulaşmayı deneyelim.

In [7]:
soup.find("yt-formatted-string", {"class":"style-scope ytd-video-renderer"})

In [8]:
soup.find("h3",{"class":"title-and-badge style-scope ytd-video-renderer"})

In [9]:
soup.find("div",{"id":"contents"})

In [10]:
soup.find("div",{"id":"container"})

<div id="container"><div id="related"><div class="autoplay skeleton-light-border-bottom"><div class="skeleton-bg-color" id="upnext"></div><div class="video-skeleton"><div class="video-details"><div class="thumbnail skeleton-bg-color"></div><div class="details flex-1"><div class="video-title text-shell skeleton-bg-color"></div><div class="video-meta text-shell skeleton-bg-color"></div></div></div></div></div><div class="video-skeleton"><div class="video-details"><div class="thumbnail skeleton-bg-color"></div><div class="details flex-1"><div class="video-title text-shell skeleton-bg-color"></div><div class="video-meta text-shell skeleton-bg-color"></div></div></div></div><div class="video-skeleton"><div class="video-details"><div class="thumbnail skeleton-bg-color"></div><div class="details flex-1"><div class="video-title text-shell skeleton-bg-color"></div><div class="video-meta text-shell skeleton-bg-color"></div></div></div></div><div class="video-skeleton"><div class="video-details">

Yaptığımız onca denemeye rağmen BeautifulSoup yardımıyla almak istediğimiz bilgilere bir türlü ulaşamadık.

> **SORU**: Bu neden olmuş olabilir?

Seçeneklerden biri; sayfayı önce Selenium ile yüklemek, sonrasında sayfanın HTML'ine BeautifulSoup ile erişmektir. Bunun için öncelikle ChromeDriver aracılığıyla YouTube arama sayfasını başlatıyoruz. 

> **NOT:** Bu işlemden sonra ekranınızda yeni bir tarayıcı açılmalıdır. Selenium'u kullanmaya devam edebilmemiz için bu pencereyi açık tutmamız gerekiyor!

In [11]:
driver = webdriver.Chrome(chromedriver)
driver.get(youtube_query)

- Şimdi, kullandığımız WebDriver yardımıyla tekrardan kaynak kodumuza erişmeye çalışalım.

In [12]:
driver.page_source

'<html style="font-size: 10px;font-family: Roboto, Arial, sans-serif;" lang="en" darker-dark-theme="" darker-dark-theme-deprecate="" dark="" system-icons="" typography="" typography-spacing=""><head><script data-original-src="/s/player/b854ee52/player_ias.vflset/en_US/miniplayer.js" nonce="qDY0mi2Vw2uennI7vZXK2A" src="/s/player/b854ee52/player_ias.vflset/en_US/miniplayer.js"></script><script data-original-src="/s/player/b854ee52/player_ias.vflset/en_US/remote.js" nonce="qDY0mi2Vw2uennI7vZXK2A" src="/s/player/b854ee52/player_ias.vflset/en_US/remote.js"></script><script data-original-src="/s/player/b854ee52/player_ias.vflset/en_US/offline.js" nonce="qDY0mi2Vw2uennI7vZXK2A" src="/s/player/b854ee52/player_ias.vflset/en_US/offline.js"></script><script data-id="_gd" nonce="qDY0mi2Vw2uennI7vZXK2A">window.WIZ_global_data = {"MuJWjd":false,"nQyAE":{},"oxN3nb":{"1":false}};</script><meta http-equiv="origin-trial" content="ApvK67ociHgr2egd6c2ZjrfPuRs8BHcvSggogIOPQNH7GJ3cVlyJ1NOq/COCdj0+zxskqHt9Hg

In [13]:
soup = BeautifulSoup(driver.page_source, "html.parser")

Ve tekrardan `BeautifulSoup` kullanarak videoların başlıklarına ulaşmaya çalışalım.

In [14]:
soup.find("h3",{"class":"title-and-badge style-scope ytd-video-renderer"})

<h3 class="title-and-badge style-scope ytd-video-renderer">
<ytd-badge-supported-renderer class="style-scope ytd-video-renderer" collection-truncate="" disable-upgrade="" hidden="">
</ytd-badge-supported-renderer>
<a aria-label="How to Become a Data Scientist in 2024? (complete roadmap) by Sundas Khalid 39,524 views 3 weeks ago 14 minutes, 10 seconds" class="yt-simple-endpoint style-scope ytd-video-renderer" href="/watch?v=mrOIT6v8_0g&amp;pp=ygUeaG93IHRvIGJlY29tZSBhIGRhdGEgc2NpZW50aXN0" id="video-title" title="How to Become a Data Scientist in 2024? (complete roadmap)">
<yt-icon class="style-scope ytd-video-renderer" hidden="" id="inline-title-icon"><!--css-build:shady--><!--css-build:shady--></yt-icon>
<yt-formatted-string aria-label="How to Become a Data Scientist in 2024? (complete roadmap) by Sundas Khalid 39,524 views 3 weeks ago 14 minutes, 10 seconds" class="style-scope ytd-video-renderer">How to Become a Data Scientist in 2024? (complete roadmap)</yt-formatted-string>
</a>
</h3

In [15]:
soup.find("h3",{"class":"title-and-badge style-scope ytd-video-renderer"}).text.strip()

'How to Become a Data Scientist in 2024? (complete roadmap)'

In [16]:
soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"})

[<a aria-label="How to Become a Data Scientist in 2024? (complete roadmap) by Sundas Khalid 39,524 views 3 weeks ago 14 minutes, 10 seconds" class="yt-simple-endpoint style-scope ytd-video-renderer" href="/watch?v=mrOIT6v8_0g&amp;pp=ygUeaG93IHRvIGJlY29tZSBhIGRhdGEgc2NpZW50aXN0" id="video-title" title="How to Become a Data Scientist in 2024? (complete roadmap)">
 <yt-icon class="style-scope ytd-video-renderer" hidden="" id="inline-title-icon"><!--css-build:shady--><!--css-build:shady--></yt-icon>
 <yt-formatted-string aria-label="How to Become a Data Scientist in 2024? (complete roadmap) by Sundas Khalid 39,524 views 3 weeks ago 14 minutes, 10 seconds" class="style-scope ytd-video-renderer">How to Become a Data Scientist in 2024? (complete roadmap)</yt-formatted-string>
 </a>,
 <a aria-label="How to Become a Data Scientist in 2024 by 365 Data Science 116,730 views 7 months ago 8 minutes, 4 seconds" class="yt-simple-endpoint style-scope ytd-video-renderer" href="/watch?v=dBpsI-aMfR8&amp;

In [17]:
for title in soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"}):
    print(title.text.strip())

How to Become a Data Scientist in 2024? (complete roadmap)
How to Become a Data Scientist in 2024
FASTEST Way to Learn Data Science and ACTUALLY Get a Job
How I Became A Data Scientist (No CS Degree, No Bootcamp)
How I'd Learn Data Science In 2023 (If I Could Restart) | A Beginner's Roadmap
🔥 Roadmap to Become a Data Scientist | How to Become a Data Scientist in 2023 | Simplilearn
how to learn Data Science from scratch in 2023
FASTEST Way to Become a Data Scientist and Actually Get a Job
What I *actually* do as a data analyst | salary, job, harsh reality
"Data Science is Dying"
What is Data Science? | Completely RoadMap | Simply Explained
Fastest Way To Become a Data Analyst
Top FREE Resources! 🔥 2024 Ultimate Roadmap: Data Science & Data Analyst 📚💥
FASTEST Way to Become a Data Analyst and ACTUALLY Get a Job
How I'd Learn to be a Data Analyst in 2024
How to Become a Data Analyst in 2024? (complete roadmap)
Data Science Roadmap 2024 | Data Science Weekly Study Plan | Free Resources to B

> **SORU**: Ama elimizde sadece 20 video başlığımız var? Aslında Youtube'da veri bilimiyle bir sürü video var?

### Sayfalardaki Etkileşimler

Selenium kullanarak normalde bizim sadece dışarıdan müdahalede bulunarak gerçekleştirebildiğimiz etkileşimler de kurabiliriz. Örneğin,

- Belli linkleri tıklama
- Boş hücrelere inputlar girme
- Kaydırma
- Sürekle-Bırak

Eğer daha fazla veri bilimi video başlığı istiyorsak, daha fazla videonun sayfa tarafından yüklenebilmesi için ekranın altına doğru kaydırma yapmamız gerekir.

In [18]:
for i in range(5):

    driver.execute_script("window.scrollTo(0, document.documentElement.scrollHeight);") # Kaydırma İşlemi
    
    time.sleep(2) # Her kaydırma işleminden sonra 2 saniye bekle

In [19]:
soup = BeautifulSoup(driver.page_source, "html.parser")

In [20]:
for title in soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"}):
    print(title.text.strip())

How to Become a Data Scientist in 2024? (complete roadmap)
How to Become a Data Scientist in 2024
FASTEST Way to Learn Data Science and ACTUALLY Get a Job
How I Became A Data Scientist (No CS Degree, No Bootcamp)
How I'd Learn Data Science In 2023 (If I Could Restart) | A Beginner's Roadmap
🔥 Roadmap to Become a Data Scientist | How to Become a Data Scientist in 2023 | Simplilearn
how to learn Data Science from scratch in 2023
FASTEST Way to Become a Data Scientist and Actually Get a Job
What I *actually* do as a data analyst | salary, job, harsh reality
"Data Science is Dying"
What is Data Science? | Completely RoadMap | Simply Explained
Fastest Way To Become a Data Analyst
Top FREE Resources! 🔥 2024 Ultimate Roadmap: Data Science & Data Analyst 📚💥
FASTEST Way to Become a Data Analyst and ACTUALLY Get a Job
How I'd Learn to be a Data Analyst in 2024
How to Become a Data Analyst in 2024? (complete roadmap)
Data Science Roadmap 2024 | Data Science Weekly Study Plan | Free Resources to B

- Süper! ChromeDriver bizim dışarıdan müdahale etmemize gerek kalmadan kaydırma işlemlerini kendi gerçekleştirdi ve bu sayede artık elimizdeki daha çok video başlığı var :)

Peki, en baştan tamamen WebDriver'ımızın kontrolünde olan bir arama yapmak istesek bunu nasıl yapacağız?

In [21]:
from selenium.webdriver.common.by import By

# Arama çubuğunun XPATH'i
search_box = driver.find_element(By.XPATH, '//input[@id="search"]')

# Önceki yaptığımız aramayı temizleme
search_box.clear()

# Yeni arama oluşturma
search_box.send_keys("machine learning")

# Aramayı gerçekleştirme
search_box.send_keys(Keys.RETURN)

Çok güzel `machine learning` aramamızı youtube üzerinden gerçekleştirdik. Peki karşıma gelen videolara ekstra bir filtre uygulamak istersem?

In [24]:
# Filtreleme butonunun XPATH'İ
filter_button = driver.find_element(By.XPATH, '//div[@id="filter-button"]')
filter_button.click()

In [25]:
# 4 dakikadan kısa olan videoları filtreleme
short_video = driver.find_element(By.XPATH, '//div[@title="Search for Under 4 minutes"]')
short_video.click()

Artık sayfa kaynağını daha önce olduğu gibi `BeautifulSoup` ile ayrıştırabilir veya doğrudan istediğimiz içerikleri alabiliriz. Örneğin, ilk kısa machine learning videosunun bazı özellikleri almaya çalışalım.

In [26]:
soup = BeautifulSoup(driver.page_source, "html.parser")

Şimdi de video başlıklarına erişmeye çalışalım.

In [28]:
soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"})

[<a aria-label="Machine Learning Explained in 100 Seconds by Fireship 481,979 views 2 years ago 2 minutes, 35 seconds" class="yt-simple-endpoint style-scope ytd-video-renderer" href="/watch?v=PeMlggyqz0Y&amp;pp=ygUQbWFjaGluZSBsZWFybmluZw%3D%3D" id="video-title" title="Machine Learning Explained in 100 Seconds">
 <yt-icon class="style-scope ytd-video-renderer" hidden="" id="inline-title-icon"><!--css-build:shady--><!--css-build:shady--></yt-icon>
 <yt-formatted-string aria-label="Machine Learning Explained in 100 Seconds by Fireship 481,979 views 2 years ago 2 minutes, 35 seconds" class="style-scope ytd-video-renderer">Machine Learning Explained in 100 Seconds</yt-formatted-string>
 </a>,
 <a aria-label="What is Machine Learning? by OxfordSparks 511,936 views 7 years ago 2 minutes, 19 seconds" class="yt-simple-endpoint style-scope ytd-video-renderer" href="/watch?v=f_uwKZIAeM0&amp;pp=ygUQbWFjaGluZSBsZWFybmluZw%3D%3D" id="video-title" title="What is Machine Learning?">
 <yt-icon class="s

In [27]:
for title in soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"}):
    print(title.text.strip())

Machine Learning Explained in 100 Seconds
What is Machine Learning?
What is Machine Learning?
Why Linear regression for Machine Learning?
Machine Learning | What Is Machine Learning? | Machine Learning Basics | 2023 | Simplilearn
How to learn AI and ML in 2024 - A complete roadmap
3 types of bias in AI | Machine learning
Microsoft Machine learning Quiz 2? #machinelearning #microsoft #quiz
Deep Learning Cars
Amazon ML Services Overview | Amazon Machine Learning  | AWS AI ML services | AWS for Beginners
Classification vs. Regression in Machine Learning
Introduction To Machine Learning -  Week 3 Answers Solution 2024 | NPTEL | SWAYAM
TensorFlow in 100 Seconds
MarI/O - Machine Learning for Video Games
Machine Learning Fundamentals: Bias and Variance
What is Machine Learning? | Machine Learning Basics | Machine Learning Tutorial | Edureka
Supervised vs Unsupervised vs Reinforcement Learning | Machine Learning Tutorial | Simplilearn
How I use Machine Learning as a Data Analyst
The Mathematic

In [29]:
titles = []
for title in soup.find("div", {"id":"contents"}).findAll("a",{"id":"video-title"}):
    titles.append(title.text.strip())
    
titles

['Machine Learning Explained in 100 Seconds',
 'What is Machine Learning?',
 'What is Machine Learning?',
 'Why Linear regression for Machine Learning?',
 'Machine Learning | What Is Machine Learning? | Machine Learning Basics | 2023 | Simplilearn',
 'How to learn AI and ML in 2024 - A complete roadmap',
 '3 types of bias in AI | Machine learning',
 'Microsoft Machine learning Quiz 2? #machinelearning #microsoft #quiz',
 'Deep Learning Cars',
 'Amazon ML Services Overview | Amazon Machine Learning  | AWS AI ML services | AWS for Beginners',
 'Classification vs. Regression in Machine Learning',
 'Introduction To Machine Learning -  Week 3 Answers Solution 2024 | NPTEL | SWAYAM',
 'TensorFlow in 100 Seconds',
 'MarI/O - Machine Learning for Video Games',
 'Machine Learning Fundamentals: Bias and Variance',
 'What is Machine Learning? | Machine Learning Basics | Machine Learning Tutorial | Edureka',
 'Supervised vs Unsupervised vs Reinforcement Learning | Machine Learning Tutorial | Simpl

Sıra youtuberlarda :)

In [30]:
soup.find("div", {"id":"contents"}).findAll("a",{"class":"yt-simple-endpoint style-scope yt-formatted-string"})

[<a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@365DataScience" spellcheck="false">365 Data Science</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@Fireship" spellcheck="false">Fireship</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@Fireship" spellcheck="false">Fireship</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@OxfordSparks" spellcheck="false">OxfordSparks</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@OxfordSparks" spellcheck="false">OxfordSparks</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@GCFLearnFree" spellcheck="false">LearnFree</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@GCFLearnFree" spellcheck="false">LearnFree</a>,
 <a class="yt-simple-endpoint style-scope yt-formatted-string" dir="auto" href="/@IBM

In [31]:
creators = []
for creator in soup.find("div", {"id":"contents"}).findAll("a",{"class":"yt-simple-endpoint style-scope yt-formatted-string"}):
    creators.append(creator.text.strip())
    
creators

['365 Data Science',
 'Fireship',
 'Fireship',
 'OxfordSparks',
 'OxfordSparks',
 'LearnFree',
 'LearnFree',
 'IBM Technology',
 'IBM Technology',
 'Simplilearn',
 'Simplilearn',
 'Python Programmer',
 'Python Programmer',
 'Google',
 'Google',
 'AI Asaan hAI',
 'AI Asaan hAI',
 'Samuel Arzt',
 'Samuel Arzt',
 'KnoDAX',
 'KnoDAX',
 'Exponent',
 'Exponent',
 'Coding Solutions',
 'Coding Solutions',
 'Fireship',
 'Fireship',
 'SethBling',
 'SethBling',
 'StatQuest with Josh Starmer',
 'StatQuest with Josh Starmer',
 'edureka!',
 'edureka!',
 'Simplilearn',
 'Simplilearn',
 'Luke Barousse',
 'Luke Barousse',
 'Zach Star',
 'Zach Star',
 'edureka!',
 'edureka!']

- Burada bir sorun var video içeriklerini paylaşan hesaplar karşımıza 2 defa gelmiş. Hadi bunun nedenini araştıralım.

In [32]:
creators = []
for creator in soup.find("div", {"id":"contents"}).findAll("a",{"class":"yt-simple-endpoint style-scope yt-formatted-string"}):
    if len(creators) % 2 == 0:
        creators.append(creator.text.strip())
    else:
        creators.append("Empty")

creators_updated = [value for value in creators if value != "Empty"]
creators_updated

['365 Data Science',
 'Fireship',
 'OxfordSparks',
 'LearnFree',
 'IBM Technology',
 'Simplilearn',
 'Python Programmer',
 'Google',
 'AI Asaan hAI',
 'Samuel Arzt',
 'KnoDAX',
 'Exponent',
 'Coding Solutions',
 'Fireship',
 'SethBling',
 'StatQuest with Josh Starmer',
 'edureka!',
 'Simplilearn',
 'Luke Barousse',
 'Zach Star',
 'edureka!']

Neyse ki biz Python biliyoruz :) Şimdi de görüntülenme sayılarını elde etmeye çalışalım.

In [33]:
soup.find("div", {"id":"contents"}).findAll("span",{"class":"inline-metadata-item style-scope ytd-video-meta-block"})

[<span class="inline-metadata-item style-scope ytd-video-meta-block">481K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">2 years ago</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">511K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">7 years ago</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">103K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">505K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">255K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">215K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">271K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">147K views</span>,
 <span class="inline-metadata-item style-scope ytd-video-meta-block">79K views</span>,
 <span class="inline-metadata-i

- Sanırım burada da benzer bir durum var. Hadi bunu da istediğimiz gibi düzenleyelim.

In [34]:
views = []
for view in soup.find("div", {"id":"contents"}).findAll("span",{"class":"inline-metadata-item style-scope ytd-video-meta-block"}):
    if len(views) % 2 == 0:
        views.append(view.text.strip())
    else:
        views.append("Empty")

views_updated = [value for value in views if value != "Empty"]
views_updated

['481K views',
 '511K views',
 '103K views',
 '255K views',
 '271K views',
 '79K views',
 '2.5K views',
 '147K views',
 '87K views',
 '239K views',
 '130K views',
 '143K views',
 '1M views',
 '8 views',
 '10M views',
 '11K views',
 '513 views',
 '5.1K views',
 '783K views',
 '11M views',
 '1.1M views',
 '313K views',
 '212K views',
 '109K views',
 '459K views',
 '1.3M views']

In [35]:
dates = []
for date in soup.find("div", {"id":"contents"}).findAll("span",{"class":"inline-metadata-item style-scope ytd-video-meta-block"}):
    if len(dates) % 2 == 1:
        dates.append(date.text.strip())
    else:
        dates.append("Empty")

dates_updated = [value for value in dates if value != "Empty"]
dates_updated

['2 years ago',
 '7 years ago',
 '505K views',
 '215K views',
 '147K views',
 '5 years ago',
 '23 hours ago',
 '78K views',
 '67K views',
 '13K views',
 '2 years ago',
 '7 months ago',
 '6 years ago',
 '2 days ago',
 '7 years ago',
 '6 days ago',
 '2 days ago',
 '4 days ago',
 '1 year ago',
 '8 years ago',
 '5 years ago',
 '5 years ago',
 '3 years ago',
 '1 year ago',
 '5 years ago',
 '5 years ago']

> **NOT:** Eğer birden fazla element seçimi yapmak istiyorsak, `driver.find_elements(...)` fonksiyonunu kullanabiliriz, bu bize tüm eşleşen elementlere ait çıktıları döndürecektir.

Eğer WebDriver kullanarak yapacağımız işlemleri tamamladıysak, çıkmadan önce driverımızı kapatmayı unutmuyoruz :)

In [36]:
driver.close()

Tüm tarayıcı oturumlarının kapatıldığından emin olmak için de çıkış yapabiliriz.

In [37]:
driver.quit()